Это домашка сделана на меньшем объёме данных - 20 000, чтобы мой ноутбук не кашлял кровью.  Я использую второй столбец как корпус, а первый - как запросы. Не будет работать без уже распакованног файла сданными

In [1]:
import csv
import pymorphy2
import string
import re
from math import log
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

morph = pymorphy2.MorphAnalyzer()
vectorizer1 = CountVectorizer(binary = True)
vectorizertf = TfidfVectorizer(use_idf=False)

In [2]:
def get_texts():
    corpus = []
    inquiery = []
    lenghths = []
    scores = []
    normal = []

    with open('quora_question_pairs_rus.csv', encoding = 'utf-8') as csvfile:
        readCSV = csv.reader(csvfile, delimiter=',')
        for row in readCSV:
            normal.append(row[2])
            text = preproc(row[2])
            corpus.append(text)
            inquiery.append(row[1])
            lenghths.append(len(text.split(' ')))
            scores.append(row[3])
            if len(scores) == 20000:
                return [corpus, inquiery, lenghths, scores, normal]

def preproc(data):                      # препроцессинг (убираем знаки препинания и числа, приводим всё к начальной форме)
            data = data.split()        
            text = ''                   # числа есть только в тех информации, в самом скрипте все числа пишутся буквами
            for word in data:
                word = word.strip('[!,.?"]')
                p = morph.parse(word.strip())[0]
                p = p.normal_form
                if p != '-':
                    if re.search(r'\d', p) == None:
                        text  = text + ' ' + p
            return text[1:]    

In [3]:
data = get_texts()

In [4]:
corpus_texts, inquiery_texts, lenghths, scores, normal_texts =  data[0][1:], data[1][1:], data[2][1:], data[3][1:], data[4][1:]
del data

In [5]:
print(corpus_texts[1])
print(inquiery_texts[1])
print(scores[1])

как повысить скорость интернет путём взлом через dns
как я могу увеличить скорость моего интернет-соединения, используя vpn
0


In [6]:
avgdl = np.mean(lenghths) 
k = 2
b = 0.75

In [7]:
corpus_matrix1 = vectorizer1.fit_transform(corpus_texts)
voc = vectorizer1.get_feature_names()
N = len(corpus_matrix1.getnnz(axis = 1))
n = corpus_matrix1.sum(axis=0)
n = n.tolist()[0]

In [8]:
idf = []
for i in range(len(voc)):
    idf_p = log((N-n[i]+0.5) / (n[i]+0.5))
    if idf_p < 0:
            idf_p = 0
    idf.append(idf_p)

In [9]:
del corpus_matrix1

In [10]:
tf = vectorizertf.fit_transform(corpus_texts)

In [11]:
tf = tf.toarray()

In [12]:
additional = []
for i  in lenghths:
    res = k * (1-b+b*(i/avgdl))
    additional.append(res)

In [13]:
k1 = k + 1
for i in range(N):
    for j in range(len(voc)):
        tf[i][j] = (tf[i][j]*k1)/(tf[i][j] + additional[i]) * idf[j]

In [14]:
del additional

Теперь перейдём к имплиминтациям  поиска

Вот **быстрый** вариант для **5**

In [158]:
def search_mat( inquiery, voc):
    inq = preproc(inquiery)
    vec = np.zeros((len(voc)))
    for word in inq.split(' '):
        if word in voc:
            index = voc.index(word)
            vec[index] = 1
    res = np.dot(tf,vec)
    results = np.argsort(res)[::-1][:5]
    for i in results:
        print(normal_texts[i])
    return

In [159]:
search_mat('правительство индии',voc)


как работает правительство Индии
почему правительство Индии запрещает все
какая разница между парламентом и правительством Индии
не принял одобрение правительства
каковы характеристики тоталитарного правительства


Вот доп. функция для медленного поисковика

In [155]:
def bm25_f(inquiery, doc, voc):
    res = 0
    for word in inquiery.split(' '):
        try:
            index = voc.index(word)
        except ValueError:
            res += 0
        else:
            res += tf[doc][index]
    return res

А вот и сам поисковик (выдающий **пять** лучших результатов, через **цикл**)

In [156]:
def search_for(inquiery, N, voc):
    d = {}
    inq = preproc(inquiery)
    for i in range(N):
        d[i] = bm25_f (inq, i, voc)
    res = sorted(d, key=d.get, reverse=True)[:5]
    for i in res:
        print(normal_texts[i])
    return

In [157]:
search_for('правительство индии', N, voc )

как работает правительство Индии
почему правительство Индии запрещает все
какая разница между парламентом и правительством Индии
каковы характеристики тоталитарного правительства
не принял одобрение правительства


#  Задание 1

In [160]:
import time
start_time = time.time()

for inquiery in inquiery_texts:
    search_mat(inquiery,voc)
    
#тут еще будут печаться ответы - сорьки   
print("--- %s seconds ---" % (time.time() - start_time))

какова история гигиены
какова история напстера
каковы лучшие в истории
какова ваша история неудачи
какова история организованных браков
как настроить vpn
как я могу увеличить скорость записи
как я могу увеличить свою скорость в помещении
как увеличить мой рост после 22
как увеличить мой рост после 16
почему я не могу решить
как я могу решить 2 ^ 2 5
как решить многочлены
как чувствуешь себя одиноким
как я могу решить ocd
метан Ванкувер ва
как я растворяю сахар в холодной воде
каковы используются соли сельдерея
как соль тает лед и снег так быстро
как вы производите углеродное волокно
Я тройная луна-козерог и восхождение в козероге, что это говорит обо мне
что означает любовь к козерогам
как заменить прокладку крышки клапана
что это значит, когда кто-то говорит это
что правильно: говорить или говорить с
я должен купить новый ноутбук
какой ноутбук я должен купить
какой ноутбук я должен купить
я должен купить битву 4 в лучшем случае купить
какой ноутбук я должен купить под 60000
что я долж

звездные войны переоценены
кто является отцом Дарта Вейдера
почему Дарт Вейдер пытался убить Лука
почему это называется звездными войнами
как йодские звездные войны стали джедаями
что происходит после смерти
которые лучше водители женщина или мужчина
что такое эмоциональная чувствительность
что происходит после сдачи крови
что происходит после смерти человека
какие продукты из сырой нефти
почему цена на сырую нефть снижается
какие факторы влияют на уровень сырой нефти
что такое нефть
какие примеры сравнений
как подружиться
как мне подружиться как застенчивый социальный неуклюжий интроверт
что такое хороший способ подружиться с иностранцами, я китайский студент
Я 35-летняя женщина, я чувствую себя одинокой и не имею друзей, чтобы поговорить или выйти, как я могу подружиться
как жизнь
как учебный материал для клата из пусковой установки
как начать профессиональное кодирование
что значит быть профессиональным
подготовка трансурановых элементов
какое оборудование требуется для установки ma

какие хорошие сайты для физики
какие лучшие справочники для химической инженерии ворот
что является лучшей книгой для химии для класса 11
который является лучшим справочным пособием для науки класса 7 класса
Каков бизнес-справочник на золотом побережье
как социальные исследования являются инструментом национальной интеграции
как улучшить социальную жизнь в колледже
как жизнь
как технология изменяет культуру
как я могу исправить свою социальную жизнь
какие из лучших романтических фильмов на английском языке
какие лучшие романтические фильмы комедии
какие из лучших недооцененных романтических комедийных фильмов
который является лучшим романтическим фильмом
каковы некоторые из лучших романтических песен на английском языке
что вызывает кошмары, которые кажутся реальными
что вызывает континентальный дрейф
что вызывает звуки грома
что действительно вызывает старение
что вызывает смерть, вися
каковы некоторые из основных влияний абстрактного экспрессионизма
современное абстрактное искусство


почему важно сжатие изображения
структура конкурирующих ценностей
порнография форма проституции
почему степень сжатия ci-двигателей высока
какие самые сильные аргументы против существования богов
что не мусульмане ожидают от мусульман
как вы стали мусульманами
которые являются ронингами
что думают мусульмане о свинье
почему мусульмане ненавидят modi правительство
твои мечты имеют значения
почему люди считают коммунизм злым
имеет ли значение, является ли человечество злом или нет
люди имеют души
почему я так зол
что такое пассивный транспорт, какие примеры
каковы примеры пассивного переноса в клетках
какие активные вулканы
как вы делаете пассивный доход?
какие примеры грибов
волосы будут расти на лысинах
что дразнят волосы
волосы будут повреждать мои волосы
как сделать волосы естественными
как избавиться от волос на лице
что такое жизнь после выхода на пенсию
Каков наилучший способ инвестирования для выхода на пенсию в Индии?
каковы наилучшие стратегии инвестирования на пенсию
каков сти

как вы получаете удаленные чаты instagram
как я могу просмотреть удаленные instagram dms
чаты - новые приложения
как вы извлекаете удаленные прямые сообщения на instagram
какие лучшие чат-сайты
мы слишком зависим от компьютеров
как я перестаю быть зависимым от кого-то
как я могу перестать быть рассеянным
вы можете стать зависимым от pepsi max
может benadryl сделать вас зависимым
я мог бы нанять двух частных следователей, а затем заставить их следовать друг за другом
мои глаза асимметричны
если бы русская атаковала
как я могу нанять хакера
как я могу нанять хакера
как ускорители запуска дают вам финансирование
которые являются лучшими ускорителями запуска в далласе
как мне найти инвесторов для моего запуска?
делает запуск в Индии
существуют ли естественные ускорители тестостерона
как я взламываю Android-телефоны
получить доступ к анонимному вопросу
были проверены ученые
как я могу получить доступ к идентификатору вызывающего абонента на телефоне Android
iphones более безопасны, чем Andr

...

почему вы читаете книги
какие книги вам нравятся читать
какие книги следует читать
вы читаете меньше книг с тех пор, как обнаружили
какие хорошие книги нужно читать
как мне придумать идею для проекта кодирования
любые конкретные идеи для механического финального проекта
как найти домен проекта
которые придумали идею для проблемы с ледяным ведром als
как после школы придумали свой логотип
может ли Бог сделать такую ​​скалу настолько тяжелой, что он не мог ее поднять
может ли Бог сделать такой тяжелый камень, что он не может его поднять
существует ли Бог
существует ли Бог
может Бог ошибается
возможно ли иметь аллергию на воду
как я сам изучаю селен
Земля теряет воду
как вы можете преодолеть пищевые аллергии
как я должен сам научиться взлому
каковы некоторые необычные аспекты политики и правительства в Сингапуре
каковы некоторые необычные аспекты политики и правительства в Норвегии
каковы некоторые необычные аспекты политики и правительства в Швейцарии
каковы некоторые необычные аспекты п

Какова программа экзамена по экзамену?
каковы две формы литературы
каков план исследования для upsc
какое определение двусмысленности в английской литературе
как я должен начать подготовку к экзаменам upsc ias?
как я изучаю органическую химию для jee advanced
что является органическим
как я читаю химию
какую книгу я должен использовать для jie органической химии
что декантирует в химии
какие мелочи и или малоизвестные факты вы найдете интересными о denmark
какие мелочи и или малоизвестные факты вы найдете интересным о монтана
какие мелочи и или малоизвестные факты вы найдете интересными относительно estonia
какие-то малоизвестные факты о walmart
какие интересные факты о бенгалуру
какая команда выиграла ipl 9
кто выиграет ipl 2013
кто выиграет ipl 2013
кто собирается выиграть ipl 2015 csk или mi
кто собирается выиграть чемпионскую лигу 2016 17
какой малоизвестный веб-сайт вам нравится просматривать
какой лучший сайт узнать, как кодировать
как я могу узнать, кто просматривает мой профиль

какой лучший рождественский подарок вы когда-либо давали
какой лучший рождественский подарок
какие страны не празднуют Рождество
какие лучшие подарки отправить подруге
какой лучший подарок вы когда-либо получали
Каков наилучший способ начать стартап?
Каков наилучший способ начать проект?
что делает видеоролик вирусом
какой лучший способ создать успешный блог
Каков наилучший способ начать новое хобби?
Что такое взаимный фонд?
Что такое взаимный фонд?
какой лучший взаимный фонд инвестировать прямо сейчас
какие паевые фонды я могу инвестировать
стоит ли инвестировать в паевой фонд?
как я могу найти жилье для студентов в Милане
полезные сайты для студентов компьютеров
лучший ноутбук под 30000 для студентов
я найду любовь
как мне найти спокойствие
Принцип
как я могу стать богатым
как я могу стать богатым
как я могу стать богатым с 1000
как стать богатым в 2015 году
когда мы вылечим слепоту
как я могу вылечить холодную погоду
как вы вылечили свои прыщи
как вылечить депрессию без терапевта
ка

почему женщины обманывают
я слишком уродлив для подруги
белые женщины находят азиатских мужчин привлекательными
почему ямочки привлекательны
почему жена меняет
Какова цель жизни
Какова цель жизни
Какова ваша цель жизни?
Какова цель вашей жизни?
Какова цель поиска
бог психопат
как я могу идентифицировать нарциссиста
как я могу идентифицировать нарциссиста
психопаты находят детей милыми
почему психопаты и нарциссисты должны наказывать своих жертв, прежде чем отбрасывать их
каковы ваши жизненные ценности
каковы жизненные простые удовольствия
как я могу бояться перемен
как я могу бояться перемен
каковы некоторые культурные подходы к переменам в r mensrights
какой отель в Чандигархе был бы безопасен для незамужних пар без преследования сотрудников полицейских гостиниц и моральной полиции
какой отель в этом будет безопасен для незамужних пар без преследования сотрудников полиции и моральной полиции
какой отель в бхопале будет безопасен для незамужних пар без преследования сотрудников полиции

что истинное значение
в чем важность мягких вычислений
каково истинное значение любви
каково истинное определение науки
Что такое мягкий ротационный сколиоз
я могу получить короче
то, что показывает, похоже на сыновья анархии
как я могу получить признание
как я могу получить признание
как я могу получить назад
какой лучший язык программирования для новичка
какой лучший язык программирования для новичка
какие языки программирования
какой лучший язык программирования для работы
какой лучший язык программирования для изучения
то, что едят котенок
это нормально, если мой котенок много мешает
почему так много знакомств
почему так много людей, элитарных
почему консультантов платят так много
как я могу начать изучать информационную безопасность
этическая дерьмо
как мне начать изучать python
каковы этические дилеммы
является информационным этическим
Какова культура компании, например, whatsapp
это мир глупый
кто-нибудь не глупый
который на земле назвал землю
делать отношения междугородных отно

In [ ]:
start_time = time.time()

for inquiery in inquiery_texts:
    search_for(inquiery, N, voc)
    
#тут еще будут печаться ответы - сорьки
# и еще у меня ноут пока это считал отключился, но я верю, что дольше
print("--- %s seconds ---" % (time.time() - start_time))

какова история напстера
какова история гигиены
каковы лучшие в истории
какова ваша история неудачи
какова история организованных браков
как настроить vpn
как я могу увеличить скорость записи
как я могу увеличить свою скорость в помещении
как увеличить уровень моего терпения
как увеличить мой рост после 16
почему я не могу решить
как я могу решить 2 ^ 2 5
как решить многочлены
как чувствуешь себя одиноким
как я могу решить ocd
метан Ванкувер ва
как я растворяю сахар в холодной воде
каковы используются соли сельдерея
как соль тает лед и снег так быстро
как вы производите углеродное волокно
Я тройная луна-козерог и восхождение в козероге, что это говорит обо мне
что означает любовь к козерогам
как заменить прокладку крышки клапана
что это значит, когда кто-то говорит это
что правильно: говорить или говорить с
я должен купить новый ноутбук
какой ноутбук я должен купить
какой ноутбук я должен купить
я должен купить битву 4 в лучшем случае купить
какой ноутбук я должен купить под 60000
что я

лучший способ увеличить твитер-последователь
как я могу увеличить число последователей
Каков самый быстрый способ похудеть?
Каков самый быстрый способ похудеть?
как мы можем увеличить количество последователей instagram
кто является отцом Дарта Вейдера
почему Дарт Вейдер пытался убить Лука
почему Дарт сидировал убить Дарта Плэгиса
звездные войны переоценены
звездные фильмы о войнах: когда-либо принцесса-лея узнает, что дарт-вейдер - ее отец
какие советы по разрыву аренды
что может привести к разрыву копейки
что происходит после смерти
то, что означает
то, что болтается
какие продукты из сырой нефти
почему цена на сырую нефть снижается
какие факторы влияют на уровень сырой нефти
что такое нефть
какие примеры дисахаридов
как подружиться
как мне подружиться как застенчивый социальный неуклюжий интроверт
что такое хороший способ подружиться с иностранцами, я китайский студент
Я 35-летняя женщина, я чувствую себя одинокой и не имею друзей, чтобы поговорить или выйти, как я могу подружиться


в чем разница между
разница между и есть
в чем разница между 0 0 и 1 0
в чем разница между 1080i и 1080p
в чем разница между и
который является лучшим игровым ноутбуком под 50000
лучший ноутбук под 30000
который является лучшим игровым ноутбуком под rs 60000
который является лучшим игровым ноутбуком под 40 000 рс
который является лучшим ноутбуком под 40000
каков ваш обзор следующего воина: полигоны - часть 5
каков ваш обзор следующего воина: полигоны - часть 1
каков ваш обзор машиностроения
Каков ваш обзор индуизма?
Каков ваш обзор фильма i 2015
какие хорошие сайты для физики
какие лучшие справочники для химической инженерии ворот
что является лучшей книгой для химии для класса 11
который является лучшим справочным пособием для науки класса 7 класса
Каков бизнес-справочник на золотом побережье
как социальные исследования являются инструментом национальной интеграции
как улучшить социальную жизнь в колледже
как жизнь
как технология изменяет культуру
как я могу исправить свою социальную 

как лучше всего вести переговоры
какие советы для переговоров с тайным нарциссистом
кто, по-твоему, ты был в прошлой жизни?
почему существует шестой раздел кванта в экзамене gre
кто выиграл прошлую ночь Майк Пенс или tim kaine vp debate
как зарегистрировать домен
как найти домен проекта
мой IP-адрес
что это домены существуют
как вы находите свой IP-адрес wifi
почему меня привлекают пожилые мужчины
почему меня привлекают пожилые мужчины
почему мужчины так привлекают женщин груди
женщины привлекают к юлианской персоне
пожилые мужчины находят 18-летних девушек привлекательными
что является самым сильным шнуром кевлара
какие самые сильные аргументы против существования богов
насколько силен невероятный толчок
которые являются самыми сильными персонажами драконьего шара
почему скорпион считается самым сильным знаком зодиака
что не мусульмане ожидают от мусульман
как вы стали мусульманами
которые являются ронингами
что думают мусульмане о свинье
почему мусульмане ненавидят modi правительство

каково это жить в Ливии
Каково это жить в Шанхае?
Каково это - жить в Сан-Франциско
Каково это - жить в Сан-Франциско
каково это жить в городе Нью-Йорк
которые являются успешными женщинами
кого вы считаете лучшим актером робер де ниро или аль-пасино
является более известным, чем
какая самая успешная религия
которые являются ронингами
почему некоторые люди предпочитают жить с маленькой семьей
почему люди предпочитают открывать перенос
почему некоторые люди атеисты
почему некоторые люди атеисты
почему некоторые люди окрашены
какие хорошие методы поцелуя
собаки плотоядные животные
животные понимают эмоции
как животные общаются
что французский французский поцелуй
как вы получаете удаленные чаты instagram
как я могу просмотреть удаленные instagram dms
чаты - новые приложения
как вы извлекаете удаленные прямые сообщения на instagram
какие лучшие чат-сайты
мы слишком зависим от компьютеров
как я перестаю быть зависимым от кого-то
как я могу перестать быть рассеянным
вы можете стать зависимым 

...

как работает словарь com
какие почтовые индексы в зоне залива
могут хинди слова получить место в оксфордском словаре
когда Китай занимал маньчжурию
Какой лучший бесплатный офлайн-словарь iphone app
почему я не чувствую гнев
мононуклеоз вообще полностью уходит
почему я не чувствую угрызений совести
почему мы чувствуем голод
растения чувствуют боль
сколько минут йоги можно сделать за один день
сколько делает бизнес-аналитик
сколько зарабатывает youtube в день
сколько времени я должен посвятить день исследованиям
сколько делают инвестиционные банкиры
почему моя собака укусила меня
какая порода моей собаки
почему моя собака вытирает мне задницу
почему собаки валяют хвосты
почему собаки мочат автомобили
как я могу получить серьезное растяжение
как вы лечите акне
как лечить гипервентиляцию алкалозом
тяжелая работа всегда окупается
как избавиться от тяжелой перхоти
какие симптомы серьезного крика на шее
можно лечить рак в непале
как вы выдыхаете крик
как вы лечите акне
как лечить гипервентиля

что считает Владимир Владимирович путать с НАТО
является российским сайдингом с Пакистаном
как я могу выйти к моей семье и друзьям
как сделать друга?
каковы преимущества совместной семьи
как начать писать собственный компилятор
жена снова обманет
как я начинаю писать
как я пишу статьи
как я пишу письмо
что существовало до Большого Взрыва
что существовало до Большого Взрыва
как вселенная выглядела до Большого Взрыва
действительно ли существовало до Большого Взрыва
какие столкновения элементов вызвали большой взрыв
как чувствуешь себя одиноким
делать отношения междугородных отношений
почему люди чувствуют себя одинокими
почему я иногда чувствую себя одиноким
как открыто открытые отношения
когда я должен начать подготовку к экзамену гражданской службы
как я могу начать подготовку к экзамену государственной службы
как начать подготовку к экзаменам по гражданским услугам
что такое экзамен по гражданской службе
как мне начать подготовку к экзамену по гражданским услугам
каковы неинвазивные с

что является лучшим способом инвестировать в недвижимость
что такое нефть
который владеет природными факторами
каковы наилучшие природные средства от холода
что является лучшим способом создания ценности
почему quora com anti-bjp и pro-aap
это microsoft surface pro 4 worth buy
является macbook pro 2016 завышенным
почему я чувствую, что новости zee - это pro bjp modi все время
Каков ваш обзор macbook pro 2016
что является хорошим источником для изучения математики
которые являются лучшими источниками для изучения хинди
что является лучшим источником для изучения python
какое лучшее время для изучения
Квора - лучший источник знаний
как бы вы описали волны
Как бы вы описали свой стиль
как бы вы описали идеального парня?
как бы вы определили человека
как бы вы определили человека
возможно ли иметь аллергию на воду
возможно ли хранить энергию молнии
возможно ли хранить энергию молнии
возможно ли выбраться из друга?
возможно ли наращивание мышц после 35
почему барак Обама так важен для мира


лучший способ избавиться от прыщей
лучший способ избавиться от метадона
как избавиться от блох
как мне избавиться от жира
как мне избавиться от желе
каковы должны быть ожидания isro от 7 платёжной комиссии
какова сила 9 карт в магии: сбор
безопасно использовать
какие компьютеры используют linux
как я могу использовать quora для зарабатывания денег
какова научная причина посещения храмов
каково значение колоколов в индуистских храмах
каково нынешнее научное мышление о причине гомосексуализма
есть ли какое-либо научное доказательство существования призраков
в чем причина ww1
разрешено обрезание в исламе
что такое ислам
как обрезание делается с девушками
почему преступление требует наказания
как люди обращаются в ислам
где я могу получить услуги профессиональных фотостудий в Сидней
где я могу получить фотобумаги лучшего качества в Сидней
где я могу получить лучшие услуги фестиваля dj в Сидней
где я могу получить разнообразные услуги печати конвертов в Сидней
где я могу получить услуги по 

что такое гравитация
почему лед легче воды
как измеряется гравитация других планет
является гравитацией закона или теории
можно будет создать гравитацию без массы
как работает юбка
что значит
что значит
как мне поднять iq
что значит в java
где в нас продаются рубашки ханы
каждый нарциссист
сколько игроков покидают профессиональный бейсбол каждый год
какова ваша новая резолюция 2017 года
это 1290 на новом 2015 году 16 пс.
как вы смотрите транссексуалов
вы используете quora
как вы смотрите на получение валмарта
как вы отправляете запрос друга на instagram
когда вы используете quora
как я тренирую белые питбуллы
как я тренирую белые питбуллы
я могу заменить белый сахар на коричневый
как вы тренируете домашнее животное?
как увлажняют предотвращающие пятна
в чем разница между
в чем разница между 0 0 и 1 0
в чем разница между 1080i и 1080p
в чем разница между и
в чем разница между мной и мной?
что самый сюрреалистический вопрос о quora
каковы некоторые из самых странных вопросов, заданных в 

перемножение на матрицу, правда, работает сильно быстрее

# Задание 2

In [27]:
def search10(inquiery, N, voc):
    d = {}
    inq = preproc(inquiery)
    for i in range(N):
        d[i] = bm25_f (inq, i, voc)
    res = sorted(d, key=d.get, reverse=True)[:10]
    for i in res:
        print(normal_texts[i], '    результат:', d[i])

In [28]:
search10('рождественские каникулы', N, voc )

каков ваш рождественский список     результат: 7.438534445830369
какой лучший рождественский подарок     результат: 7.438534445830369
как я могу провести летние каникулы осмысленно     результат: 5.365484239973764
какой лучший рождественский подарок вы когда-либо давали     результат: 4.355020046598063
я не хочу покупать маме рождественский подарок, что я должен делать     результат: 3.1175849918074796
вы можете найти рождественскую коляду, которую пела женщина в 1995 году 6 в очень грустном голосе     результат: 2.3089523138721044
я делаю бакалавров в области компьютерных наук, я сделаю с моим 4-м семестром за несколько дней. У меня есть 3 месяца летних каникул вперед. Какой лучший способ я могу использовать эти 3 месяца, чтобы я мог приземлиться на хорошую стажировку в будущем на вершине компания с надписью типа microsoft google facebook и т. д.     результат: 0.43368348190130357
что произойдет, если правительство Индии украдет кохинор кох-и-ноор-алмаз назад     результат: 0.0
как по

Как видно, 10 не наберётся. Вероятно, в связи с тем, что я считаю на 20к

#  Задание 3

Это задание работает невероятно долго

для этого задания разработаем поиск который ничего не принтит, а вместо этого ретёрнит res

In [ ]:
def search_np( inquiery, voc):
    inq = preproc(inquiery)
    vec = np.zeros((len(voc)))
    for word in inq.split(' '):
        if word in voc:
            index = voc.index(word)
            vec[index] = 1
    res = np.dot(tf,vec)
    return np.argsort(res)[::-1][:5]

в обеих колонках есть дубликаты, так что....

In [ ]:
d ={}
for i in range(1000):
    if int(scores[i]) == 1:
        if inquiery_texts[i] in d.keys():
            d[inquiery_texts[i]].append(normal_texts[i])
        else:
            d[inquiery_texts[i]] = [normal_texts[i]]

In [ ]:
d

In [ ]:
# результат с нормальными параметрами
count = 0
for i in range(1000):
    #print(i)
    res = search_np(inquiery_texts[i], N, voc)
    c = 0
    if  inquiery_texts[i] in d.keys():
        for j in res:
            if normal_texts[j] in d[inquiery_texts[i]]:
                c = 1
    count += c
    
print((count/N)*100)

 Сделаем всё для bm15

In [ ]:
k = 2
b = 0
tf = vectorizertf.fit_transform(corpus_texts)
tf = tf.toarray()

In [ ]:
additional = []
for i  in lenghths:
    res = k * (1-b+b*(i/avgdl))
    additional.append(res)

k1 = k + 1
for i in range(N):
    for j in range(len(voc)):
        tf[i][j] = (tf[i][j]*k1)/(tf[i][j] + additional[i]) * idf[j]

In [ ]:
def bm15_f(inquiery, doc, voc):
    res = 0
    for word in inquiery.split(' '):
        try:
            index = voc.index(word)
        except ValueError:
            res += 0
        else:
            res += tf[doc][index]
    return res

In [ ]:
def search5_np(inquiery, N, voc):
    d = {}
    inq = preproc(inquiery)
    for i in range(N):
        d[i] = bm15_f (inq, i, voc)
    res = sorted(d, key=d.get, reverse=True)[:5]
    return res

In [ ]:
count = 0
for i in range(1000):
    res = search5_np(inquiery_texts[i], N, voc)
    c = 0
    if  inquiery_texts[i] in d.keys():
        for j in res:
            if normal_texts[j] in d[inquiery_texts[i]]:
                c = 1
    count += c
    
print((count/N)*100)

а теперь сделаем всё для bm11

In [ ]:
k = 2
b = 1
tf = vectorizertf.fit_transform(corpus_texts)
tf = tf.toarray()

In [ ]:
additional = []
for i  in lenghths:
    res = k * (1-b+b*(i/avgdl))
    additional.append(res)

k1 = k + 1
for i in range(N):
    for j in range(len(voc)):
        tf[i][j] = (tf[i][j]*k1)/(tf[i][j] + additional[i]) * idf[j]

In [ ]:
def bm11_f(inquiery, doc, voc):
    res = 0
    for word in inquiery.split(' '):
        try:
            index = voc.index(word)
        except ValueError:
            res += 0
        else:
            res += tf[doc][index]
    return res

In [ ]:
def search5_np(inquiery, N, voc):
    d = {}
    inq = preproc(inquiery)
    for i in range(N):
        d[i] = bm11_f (inq, i, voc)
    res = sorted(d, key=d.get, reverse=True)[:5]
    return res

In [ ]:
count = 0
for i in range(1000):
    res = search5_np(inquiery_texts[i], N, voc)
    c = 0
    if  inquiery_texts[i] in d.keys():
        for j in res:
            if normal_texts[j] in d[inquiery_texts[i]]:
                c = 1
    count += c
    
print((count/N)*100)

В общем, все результаты сравнимы